In [29]:
import pandas as pd
import requests
import json
from datetime import datetime
import time
import math

### TVL de las principales chains

In [30]:
url_chain = "https://api.llama.fi/v2/historicalChainTvl/"

chains = ['Ethereum', 'Solana', 'BSC', 'Tron', 'Tron', 'Sui', 'Aptos']

# dfs = {}
dfs = []
for chain in chains:
    url = url_chain + chain
    response = requests.get(url)
    data = response.json()
    df = pd.DataFrame(data)

    df['date'] = pd.to_datetime(df['date'], unit='s')
    df.set_index('date', inplace=True)
    df.rename(columns={'tvl':chain}, inplace=True)
    dfs.append(df)

df = pd.concat(dfs)
df
    #dfs[chain] = df

#dfs
# df = pd.concat(dfs.values(), axis=1)
# df


Ethereum  Solana  BSC  Tron  Sui         Aptos
date                                                           
2018-04-27  404077.858810     NaN  NaN   NaN  NaN           NaN
2018-04-28  400585.099213     NaN  NaN   NaN  NaN           NaN
2018-04-29  429213.933200     NaN  NaN   NaN  NaN           NaN
2018-04-30  421651.156158     NaN  NaN   NaN  NaN           NaN
2018-05-01  436194.969783     NaN  NaN   NaN  NaN           NaN
...                   ...     ...  ...   ...  ...           ...
2024-11-07            NaN     NaN  NaN   NaN  NaN  8.869377e+08
2024-11-08            NaN     NaN  NaN   NaN  NaN  8.995676e+08
2024-11-09            NaN     NaN  NaN   NaN  NaN  9.191087e+08
2024-11-10            NaN     NaN  NaN   NaN  NaN  9.923553e+08
2024-11-11            NaN     NaN  NaN   NaN  NaN  1.047469e+09

[9876 rows x 6 columns]

In [31]:
import plotly.express as px

fig = px.line(df, x=df.index, y=df.columns, title="Chain TVL")
fig.update_layout(template='plotly_dark')

fig.show()

### L2 Ethereum

In [32]:
url_chain = "https://api.llama.fi/v2/historicalChainTvl/"

chains = ['Base', 'Arbitrum', 'Taiko', 'Optimism', 'Blast', 'Mantle', 'Linea', 'Scroll', 'ZKsync Era']

# dfs = {}
dfs = []
for l2 in chains:
    url = url_chain + l2
    response = requests.get(url)
    data = response.json()
    df = pd.DataFrame(data)

    df['date'] = pd.to_datetime(df['date'], unit='s')
    df.set_index('date', inplace=True)
    df.rename(columns={'tvl':l2}, inplace=True)
    dfs.append(df)

df = pd.concat(dfs)
df = df[df.index >= '2024-01-01']
    #dfs[chain] = df

#dfs
# df = pd.concat(dfs.values(), axis=1)
# df


In [33]:
import plotly.express as px

fig = px.line(df, x=df.index, y=df.columns, title="TVL L2")
fig.update_layout(template='plotly_dark')

fig.show()

---

### Variación porcentual chains TVL

In [34]:
def get_chain_data(chain):
    baseUrl = 'https://api.llama.fi/v2/historicalChainTvl/'
    chaintv = requests.get(baseUrl + chain).json()
    
    # Crear DataFrame y procesar
    df = pd.DataFrame(chaintv)
    df['date'] = pd.to_datetime(df['date'], unit='s')
    df.set_index('date', inplace=True)
    df.rename(columns={'tvl': chain}, inplace=True)
    
    # Calcular cambios porcentuales
    df['%1D'] = df[chain].pct_change(1) * 100
    df['%7D'] = df[chain].pct_change(7) * 100
    df['%30D'] = df[chain].pct_change(30) * 100
    
    # Seleccionar la última fila de cambios porcentuales
    return df[['%1D', '%7D', '%30D']].iloc[-1]


chains = ['Ethereum', 'Solana', 'BSC', 'Tron', 'Sui', 'Aptos' ,'Base', 'Arbitrum', 'Polygon', 'Optimism', 'Blast', 'Mantle', 'Linea', 'Scroll']
# Obtener los últimos cambios porcentuales para Ethereum y Solana

df_tvl = []
for chain in chains:
    chain_changes = get_chain_data(chain)
    df = pd.DataFrame({chain:chain_changes}).T
    df_tvl.append(df)

df = pd.concat(df_tvl)
df

%1D        %7D       %30D
Ethereum   3.669475  27.806747  33.132661
Solana     7.176816  30.892758  34.570118
BSC        1.453448  16.901645  13.914720
Tron       1.242255   2.739592  -6.327807
Sui        2.455634  38.766014  25.959072
Aptos      5.553873  31.233939  63.815368
Base       1.536839  25.853226  31.704727
Arbitrum   4.831081  24.961647  22.971875
Polygon    1.225027  -8.136788  19.758336
Optimism   2.416716  25.284523  17.200339
Blast      0.682144  18.655450   7.864593
Mantle     2.664902  34.872709  57.114334
Linea      3.997742  28.093608  23.420875
Scroll   -16.668875  -5.701196 -54.106156

---

### MARK CAP memecoin > 500M

In [35]:
from pycoingecko import CoinGeckoAPI
cg = CoinGeckoAPI()

In [36]:
coinsMktDataByCategory = cg.get_coins_markets(vs_currency = 'usd',category = 'meme-token',
                                    order = 'volume_desc')

coinsMktDataByCategory = pd.DataFrame(coinsMktDataByCategory)
coinsMktDataByCategory.columns

Index(['id', 'symbol', 'name', 'image', 'current_price', 'market_cap',
       'market_cap_rank', 'fully_diluted_valuation', 'total_volume',
       'high_24h', 'low_24h', 'price_change_24h',
       'price_change_percentage_24h', 'market_cap_change_24h',
       'market_cap_change_percentage_24h', 'circulating_supply',
       'total_supply', 'max_supply', 'ath', 'ath_change_percentage',
       'ath_date', 'atl', 'atl_change_percentage', 'atl_date', 'roi',
       'last_updated'],
      dtype='object')

In [37]:
df = coinsMktDataByCategory[['name','symbol', 'current_price', 'market_cap', 'price_change_24h']]
#df =df[df['market_cap'] >= 200000000]
df = df.loc[df['market_cap'] >=500000000 ]
df

name    symbol  current_price    market_cap  \
0               Dogecoin      doge       0.323212  4.709275e+10   
1              Shiba Inu      shib       0.000028  1.623125e+10   
2                   Pepe      pepe       0.000013  5.470405e+09   
3              dogwifhat       wif       3.130000  3.122877e+09   
5                  Neiro     neiro       0.002413  1.008741e+09   
6                   Bonk      bonk       0.000027  1.884683e+09   
7           BOOK OF MEME      bome       0.009457  6.504643e+08   
8                  FLOKI     floki       0.000184  1.780933e+09   
11               Notcoin       not       0.007643  7.785499e+08   
12   cat in a dogs world       mew       0.011122  9.835145e+08   
15      Goatseus Maximus      goat       0.835265  8.271522e+08   
16                 Turbo     turbo       0.008934  6.129603e+08   
17                Popcat    popcat       1.650000  1.608254e+09   
21                 Brett     brett       0.121888  1.197192e+09   
28              Mog Coin       mog       0.000002  7.689593e+08   
33                  Fwog      fwog       0.525440  5.110054e+08   
34              Gigachad      giga       0.055884  5.300914e+08   
40               SPX6900       spx       0.782311  7.270243e+08   
46  Binance-Peg Dogecoin      doge       0.320219  6.598315e+08   
63              PepeCoin  pepecoin       5.370000  6.465316e+08   

    price_change_24h  
0       5.663900e-02  
1       2.820000e-06  
2       1.020000e-06  
3       4.494970e-01  
5      -1.656620e-04  
6       2.220000e-06  
7       1.791700e-04  
8       1.006000e-05  
11     -1.725535e-05  
12      6.948900e-04  
15     -6.518539e-03  
16     -5.310041e-04  
17      2.144490e-01  
21      2.028761e-02  
28     -7.597966e-08  
33     -1.084973e-02  
34     -6.438344e-03  
40     -1.775295e-02  
46      4.961759e-02  
63      6.550890e-01

In [38]:
fig = px.pie(
    df, 
    values='market_cap', 
    names='symbol', 
    title="Market Cap Memecoins",
    color_discrete_sequence=px.colors.qualitative.Pastel  # Colores suaves para mejor visualización
)
fig.update_layout(
    showlegend=True,
    legend_title_text='Criptomonedas',
    margin=dict(t=50, b=50, l=25, r=25),
    template='plotly_dark')


fig.show()

---

### Volumen del día de hoy en los principales exchanges

In [39]:
import datetime as dt
ids= ['binance', 'coinbase-exchange']

exchangevolume = []

for exchnage in ids:
    exchgVolume = cg.get_exchanges_volume_chart_by_id(id=exchnage, days=1)
    exchgVolumeDataFrame = pd.DataFrame(exchgVolume,  columns = ['Date', exchnage])
    exchgVolumeDataFrame['Date'] = pd.to_datetime(exchgVolumeDataFrame['Date'], unit='ms')

    exchangevolume.append(exchgVolumeDataFrame.set_index('Date'))

df = pd.concat(exchangevolume, axis=1)
df

# exchgVolumeDataFrame['Date'] = exchgVolumeDataFrame['Date'].apply(
#     lambda x:dt.datetime.fromtimestamp(x/1000).strftime('%m-%d-%Y')
# )



binance       coinbase-exchange
Date                                                                
2024-11-10 20:20:00  473038.0692656193613682  68052.1085545715819606
2024-11-10 20:30:00  478060.1225613573452865   69006.384952163425159
2024-11-10 20:40:00  478459.0626101279300907  69522.0179184304930568
2024-11-10 20:50:00  484012.1710154471107056  70638.4621954298352802
2024-11-10 21:00:00  485632.4668912803397203  70841.0884797529325185
...                                      ...                     ...
2024-11-11 19:30:00  564847.1546885552114468  89224.8073395098883455
2024-11-11 19:40:00  564605.3803996928516987  89655.0256250450423846
2024-11-11 19:50:00  560827.1217435497609297  90495.2407806829404838
2024-11-11 20:00:00  561002.0710630762671265  91009.5195522754516041
2024-11-11 20:10:00  559433.6694401051623218  87410.3464373533078704

[144 rows x 2 columns]

In [40]:
df[['binance', 'coinbase-exchange']] = df[['binance', 'coinbase-exchange']].apply(pd.to_numeric)

df

binance  coinbase-exchange
Date                                                 
2024-11-10 20:20:00  473038.069266       68052.108555
2024-11-10 20:30:00  478060.122561       69006.384952
2024-11-10 20:40:00  478459.062610       69522.017918
2024-11-10 20:50:00  484012.171015       70638.462195
2024-11-10 21:00:00  485632.466891       70841.088480
...                            ...                ...
2024-11-11 19:30:00  564847.154689       89224.807340
2024-11-11 19:40:00  564605.380400       89655.025625
2024-11-11 19:50:00  560827.121744       90495.240781
2024-11-11 20:00:00  561002.071063       91009.519552
2024-11-11 20:10:00  559433.669440       87410.346437

[144 rows x 2 columns]

In [41]:
import plotly.graph_objects as go

fig = go.Figure()

# Agregar la línea para Binance en el eje primario
fig.add_trace(go.Scatter(x=df.index, y=df['binance'], mode='lines', name='binance', line=dict(color='yellow')))

# Agregar la línea para Coinbase en un eje secundario
fig.add_trace(go.Scatter(x=df.index, y=df['coinbase-exchange'], mode='lines', name='coinbase-exchange', line=dict(color='red'), yaxis="y2"))

# Configuración del diseño
fig.update_layout(
    title="Volumen Biance y coinbase Exchange",
    xaxis_title="Date",
    yaxis_title="Volumen Binance",
    yaxis2=dict(
        title="Volume Coinbase",
        overlaying='y',   # Superpone el eje secundario al eje primario
        side='right'      # Muestra el eje secundario en el lado derecho
    ),
    showlegend=True,
    legend_title_text="Exchanges",
    template="plotly_dark"
)

fig.show()